In [3]:
import os,re,json

"""---明确数据文件位置---"""
datafile = "文本文件/metadata.txt"
# 双回车分隔，记录内单回车分隔列表，首行为字段名
"""---文件位置结束---"""

def trim(string):
    string = re.sub(r"^[ \t\n]*","",string)
    string = re.sub(r"[ \t\n]*$","",string)
    return string
def FloatToInt(string):
    f = float(string)
    if abs(f-round(f))<0.01:
        f = round(f)
    return f

with open(datafile,"r",encoding="utf8") as f:
    data = f.read()
pos = data.index("\n")
field = data[:pos].strip()
appending_data = data[pos:]

with open(r"../题库0.3/Problems.json","r",encoding = "utf8") as f:
    database = f.read()
pro_dict = json.loads(database)
with open(r"../题库0.3/LessonObj.json","r",encoding = "utf8") as f:
    database = f.read()
obj_dict = json.loads(database)

#该字段列表可能需要更新
fields = ["content","objs","tags","genre","ans","solution","duration","usages","origin","edit","same","related","remark","space"]

if field in fields:
    field_type = type(pro_dict["000001"][field])
    datalist = [record.strip() for record in appending_data.split("\n\n") if len(trim(record)) > 0]
    for record in datalist:
        id = re.findall(r"^[\d]{1,}",record)[0]
        data = record[len(id):].strip()
        id = id.zfill(6)
        if not id in pro_dict:
            print("题号:",id,"不在数据库中.")
            break
        
        #字符串类型字段添加数据
        elif field_type == str and data in pro_dict[id][field]:
            print("题号:",id,", 字段:",field,"中已有该数据:",data)
        elif field_type == str and not data in pro_dict[id][field] and not field == "ans" and not field == "space":
            origin_data = pro_dict[id][field]
            new_data = trim(origin_data + "\n" + data)
            pro_dict[id][field] = new_data
            print("题号:",id,", 字段:",field,"中已添加数据:",data)
        elif field_type == str and not data in pro_dict[id][field] and field == "ans" or field == "space":
            pro_dict[id][field] = data
            print("题号:",id,", 字段:",field,"中已修改数据:",data)
        
        #数值类型字段添加数据
        elif (field_type == int or field_type == float) and abs(float(data) - pro_dict[id][field])<0.01:
            print("题号:",id,", 字段:",field,"中已有该数据:",FloatToInt(data))
        elif (field_type == int or field_type == float) and abs(float(data) - pro_dict[id][field])>=0.01:
            pro_dict[id][field] = FloatToInt(data)
            print("题号:",id,", 字段:",field,"中已修改数据:",FloatToInt(data))
        
        #列表类型字段添加数据
        elif field_type == list:
            cell_data_list = [d.strip() for d in data.split("\n")]
            for cell_data in cell_data_list:
                if cell_data in pro_dict[id][field]:
                    print("题号:",id,", 字段:",field,"中已有该数据:",cell_data)
                elif not field == "objs":
                    pro_dict[id][field].append(cell_data)
                    print("题号:",id,", 字段:",field,"中已添加数据:",cell_data)
                else:
                    if not cell_data in obj_dict and not cell_data.upper() == "KNONE":
                        print("题号:",id,", 字段:",field,"目标编号有误:",cell_data)
                    else:
                        pro_dict[id][field].append(cell_data.upper())
                        print("题号:",id,", 字段:",field,"中已添加数据:",cell_data.upper())

with open(r"../题库0.3/Problems.json","w",encoding = "utf8") as f:
    f.write(json.dumps(pro_dict,indent=4,ensure_ascii=False))

题号: 011585 , 字段: ans 中已修改数据: $(0,-2)$
